In [42]:
import pandas as pd
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import plotly.express as px
from dash import Dash, dcc, html, Input, Output


asylum = pd.read_csv('.\\Data\\Clean\\Asylum_data.csv')
asylum

country_of_origin_abbr country_of_origin_name country_of_asylum_abbr  \
0                         DZA                Algeria                    MLT   
1                         AGO                 Angola                    COD   
2                         AGO                 Angola                    NAM   
3                         BDI                Burundi                    NAM   
4                         CHN                  China                    NPL   
...                       ...                    ...                    ...   
103303                    ZWE               Zimbabwe                    POL   
103304                    ZWE               Zimbabwe                    ZAF   
103305                    ZWE               Zimbabwe                    SWE   
103306                    ZWE               Zimbabwe                    USA   
103307                    ZWE               Zimbabwe                    ZMB   

          country_of_asylum_name      region_of_asylum        category  year  \
0                          Malta                Europe         Refugee  1962   
1         Dem. Rep. of the Congo       Southern Africa         Refugee  1962   
2                        Namibia       Southern Africa         Refugee  1962   
3                        Namibia       Southern Africa         Refugee  1962   
4                          Nepal  Asia and the Pacific         Refugee  1962   
...                          ...                   ...             ...   ...   
103303                    Poland                Europe  Asylum-seekers  2024   
103304              South Africa       Southern Africa  Asylum-seekers  2024   
103305                    Sweden                Europe  Asylum-seekers  2024   
103306  United States of America              Americas  Asylum-seekers  2024   
103307                    Zambia       Southern Africa  Asylum-seekers  2024   

        count  
0           5  
1       20000  
2         277  
3          13  
4           5  
...       ...  
103303      9  
103304     89  
103305      5  
103306    641  
103307      9  

[103308 rows x 8 columns]

In [43]:
# Timeline of the afghanistan migration
def Get_Destination_by_year_df(df: pd.DataFrame, country_abbr: str) -> pd.DataFrame:
    result = df[df['country_of_origin_abbr'] == country_abbr]
    result = result.groupby(['year', 'country_of_asylum_abbr']).agg({'count' : 'sum'}).reset_index()
    result['merge_column'] = result['country_of_asylum_abbr'] + result['year'].astype(str)
    return result

def Get_countries_and_years_df(df: pd.DataFrame) -> pd.DataFrame:
    countries = df['country_of_asylum_abbr'].unique()
    years = df['year'].unique()
    result = pd.DataFrame(columns=["country", "year"])
    for country in countries:
        c_list = [country] * len(years)
        country_list_df = pd.DataFrame({"country" : c_list, "year" : years})
        result = pd.concat([result, country_list_df], ignore_index=True)
    result['merge_column'] = result['country'] + result['year'].astype(str)
    return result

## TODO: For loop at group by with if statement


def Merge_and_clean_df(destination_df: pd.DataFrame, years_df: pd.DataFrame) -> pd.DataFrame:
    final = years_df.merge(destination_df, on='merge_column', how='left')
    final[final['year_x'] != final['year_y']]
    final = final.drop(columns=['year_y', 'merge_column', 'country_of_asylum_abbr'])
    final = final.rename(columns={'year_x': 'year'})
    final['count'] = final['count'].fillna(0)
    final['cumulative_sum'] = final.groupby('country')['count'].cumsum()
    return final

def Get_ready_for_plot_df(df: pd.DataFrame, country_of_origin_abbr: str) -> pd.DataFrame:
    destination = Get_Destination_by_year_df(df, country_of_origin_abbr)
    yearly = Get_countries_and_years_df(destination)
    return Merge_and_clean_df(destination, yearly)    

def Get_total_country_migration_df(df: pd.DataFrame, country_of_origin_abbr: str) -> pd.DataFrame:
    return df[df['country_of_origin_abbr'] == country_of_origin_abbr].groupby('year').agg({'count' : 'sum'}).reset_index()

afghanistan = asylum[asylum['country_of_origin_abbr'] == 'VEN']
afghanistan.groupby('year').agg({'count' : 'sum'}).reset_index()

afghanistan

country_of_origin_abbr              country_of_origin_name  \
556                       VEN  Venezuela (Bolivarian Republic of)   
3311                      VEN  Venezuela (Bolivarian Republic of)   
3312                      VEN  Venezuela (Bolivarian Republic of)   
4391                      VEN  Venezuela (Bolivarian Republic of)   
6490                      VEN  Venezuela (Bolivarian Republic of)   
...                       ...                                 ...   
103235                    VEN  Venezuela (Bolivarian Republic of)   
103236                    VEN  Venezuela (Bolivarian Republic of)   
103237                    VEN  Venezuela (Bolivarian Republic of)   
103238                    VEN  Venezuela (Bolivarian Republic of)   
103239                    VEN  Venezuela (Bolivarian Republic of)   

       country_of_asylum_abbr     country_of_asylum_name region_of_asylum  \
556                       CHE                Switzerland           Europe   
3311                      FRA                     France           Europe   
3312                      DEU                    Germany           Europe   
4391                      DEU                    Germany           Europe   
6490                      CAN                     Canada         Americas   
...                       ...                        ...              ...   
103235                    CHE                Switzerland           Europe   
103236                    SXM  Sint Maarten (Dutch part)         Americas   
103237                    URY                    Uruguay         Americas   
103238                    URY                    Uruguay         Americas   
103239                    USA   United States of America         Americas   

                                                category  year   count  
556                                       Asylum-seekers  1973       5  
3311                                      Asylum-seekers  1984       5  
3312                                      Asylum-seekers  1984       5  
4391                                      Asylum-seekers  1986       5  
6490                                      Asylum-seekers  1989      50  
...                                                  ...   ...     ...  
103235                                    Asylum-seekers  2024      41  
103236                                    Asylum-seekers  2024       5  
103237                                    Asylum-seekers  2024     444  
103238  Other people in need of international protection  2024     775  
103239                                    Asylum-seekers  2024  116653  

[705 rows x 8 columns]

# Plotting a map that shows country of destination

In [49]:
final = Get_ready_for_plot_df(asylum, 'AFG')

fig = px.scatter_geo(final, locations="country", locationmode='ISO-3', color="country",
                     hover_name="country", size="cumulative_sum",
                     animation_frame="year",
                     projection="natural earth")

fig.show()

In [50]:
final_heat = final[final['cumulative_sum'] != 0]

fig = px.choropleth(final_heat, locations="country", locationmode='ISO-3',
                     color="cumulative_sum",
                     color_continuous_scale="Reds",
                     hover_name="country",
                     animation_frame="year",
                     projection="natural earth")

fig.show()

In [53]:
def Peak_finder(data: pd.DataFrame):
    percentaje_to_check = 0.5
    previous_value = data['count'][0]
    previous_year = data['year'][0]

    inside_peak = False
    current_highlight = {}
    # Start of the highlight:
    for index, row in data.iterrows():
        if not inside_peak:
            if previous_value > 1000:
                if (row['count'] - previous_value) > (previous_value * percentaje_to_check):
                    current_highlight = {'start': previous_year, 'end': 0}
                    inside_peak = True
        else:
            if (row['count']) <= (previous_value):
                current_highlight['end'] = row['year']
                yield current_highlight
                inside_peak = False
                current_highlight = {}
        previous_value = row['count']
        previous_year = row['year']


# Functions 
# Timeline of the afghanistan migration
def Get_Destination_by_year_df(df: pd.DataFrame, country_abbr: str) -> pd.DataFrame:
    result = df[df['country_of_origin_abbr'] == country_abbr]
    result = result.groupby(['year', 'country_of_asylum_abbr']).agg({'count' : 'sum'}).reset_index()
    result['merge_column'] = result['country_of_asylum_abbr'] + result['year'].astype(str)
    return result

def Get_countries_and_years_df(df: pd.DataFrame) -> pd.DataFrame:
    countries = df['country_of_asylum_abbr'].unique()
    years = df['year'].unique()
    result = pd.DataFrame(columns=["country", "year"])
    for country in countries:
        c_list = [country] * len(years)
        country_list_df = pd.DataFrame({"country" : c_list, "year" : years})
        result = pd.concat([result, country_list_df], ignore_index=True)
    result['merge_column'] = result['country'] + result['year'].astype(str)
    return result

## TODO: For loop at group by with if statement


def Merge_and_clean_df(destination_df: pd.DataFrame, years_df: pd.DataFrame) -> pd.DataFrame:
    final = years_df.merge(destination_df, on='merge_column', how='left')
    final[final['year_x'] != final['year_y']]
    final = final.drop(columns=['year_y', 'merge_column', 'country_of_asylum_abbr'])
    final = final.rename(columns={'year_x': 'year'})
    final['count'] = final['count'].fillna(0)
    final['cumulative_sum'] = final.groupby('country')['count'].cumsum()
    return final

def Get_ready_for_plot_df(df: pd.DataFrame, country_of_origin_abbr: str) -> pd.DataFrame:
    destination = Get_Destination_by_year_df(df, country_of_origin_abbr)
    yearly = Get_countries_and_years_df(destination)
    return Merge_and_clean_df(destination, yearly)    

def Get_total_country_migration_df(df: pd.DataFrame, country_of_origin_abbr: str) -> pd.DataFrame:
    return df[df['country_of_origin_abbr'] == country_of_origin_abbr].groupby('year').agg({'count' : 'sum'}).reset_index()

In [55]:
app2 = Dash(__name__)

countries = asylum[['country_of_origin_abbr', 'count']].groupby('country_of_origin_abbr').agg({'count': "sum"}).reset_index().sort_values('count', ascending=False)
options = countries['country_of_origin_abbr'].unique()

app2.layout = html.Div([
    html.H2('Countries', style={'text-align': "center"}),
    html.P('Select country:'),
    dcc.Dropdown(
        id="dropdown",
        options=options,
        value=options[0],
        clearable=False,
    ),
    dcc.Graph(id="line"),
    dcc.Graph(id="graph"),
    
], style={'backgroundColor':'white'})

@app2.callback(
    Output("graph", "figure"),
    Input("dropdown", "value"))

def update_bar_chart(country):
    final = Get_ready_for_plot_df(asylum, country)
    final_heat = final[final['cumulative_sum'] != 0]

    fig = px.choropleth(final_heat, locations="country", locationmode='ISO-3',
                        color="cumulative_sum",
                        color_continuous_scale="Reds",
                        hover_name="country",
                        animation_frame="year",
                        projection="natural earth")
    country_to_highlight = "USA"
    fig.add_trace(
        go.Choropleth(
            locations=[country],
            z=[1],
            colorscale=[[0, "green"], [1, "green"]],  
            showscale=False,
            hovertemplate="%{location}"
        )
    )

    return fig

@app2.callback(
    Output("line", "figure"),
    Input("dropdown", "value"))

def update_line(country):
    timeline = Get_total_country_migration_df(asylum, country)
    trace = go.Scatter(x=timeline['year'], y=timeline['count'])
    fig = go.Figure(trace)

    for peak in Peak_finder(timeline):
        fig.add_shape(type="rect",
                    x0=peak['start'], y0=0, x1=peak['end'], y1=timeline['count'].max(),
                    fillcolor="tomato", opacity=0.5,
                    layer="below", line_width=0)

    fig.update_layout(
        title=f'Total {country} asylum seeker population over the years (highlighted migration crisis)',
        xaxis={'title': {'text': "Years"}, 'showgrid':False},
        yaxis={'title': {'text': 'Asylum Seekers'}, 'rangemode': 'tozero', 'showgrid':False}
    )

    return fig



app2.run(debug=True, port=8051)